In [1]:
import lmdb
import pickle
import glob
import os
import pandas as pd
from torch_geometric.data import Data

In [ ]:
train_dir = "oc22/is2re-total/train"
train_files = sorted(glob.glob(os.path.join(train_dir, "data.*.lmdb")))

# all the properties available in the metadata pickle file
columns = [
    "sid",
    "y_relaxed",
    "bulk_id",
    "bulk_symbols",
    "miller_index",
    "traj_id",
    "slab_sid",
    "ads_symbols",
    "nads"
]

# read metadata file for bulk symbol
with open("oc22_metadata.pkl", "rb") as file:
    metadata = pickle.load(file)

all_data = []

for lmdb_file in train_files:
    env = lmdb.open(lmdb_file, readonly=True, subdir=False, lock=False)

    with env.begin() as txn:
        num_entries = txn.stat()['entries']
        print(f"Processing {lmdb_file}: {num_entries} entries")

        cursor = txn.cursor()

        for key, value in cursor:
            try:
                # load pytorch data obj manually due to the imcompatible PyG version of OC22 dataset
                data = Data.from_dict(pickle.loads(value).__dict__)

                # get target value and sid from training dataset
                sid = data.sid
                y_relaxed = data.y_relaxed

                row = {
                    "sid": sid,
                    "y_relaxed": y_relaxed
                }

                # grab rest of the data from metadata
                if sid in metadata:
                    row.update(metadata[sid])

                all_data.append(row)
            except:
                pass
    env.close()

df = pd.DataFrame(all_data, columns=columns)
df.to_csv("data/training_FULL.csv", index=False)

Processing oc22/is2re-total/train/data.0000.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0001.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0002.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0003.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0004.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0005.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0006.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0007.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0008.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0009.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0010.lmdb: 1121 entries
Processing oc22/is2re-total/train/data.0011.lmdb: 1120 entries
Processing oc22/is2re-total/train/data.0012.lmdb: 1120 entries
Processing oc22/is2re-total/train/data.0013.lmdb: 1120 entries
Processing oc22/is2re-total/train/data.0014.lmdb: 1120 entries
Processing oc22/is2re-total/train/data.0015.lmdb: 1120 

In [43]:
# get the samples with H as adsorbate
# creates a mask where True if ads is H
contains_h_adsorbate = (df['ads_symbols'] == 'H') & (df['nads'] == 1)

# robust mask for rows with no adsorbates: handles None/NaN, empty lists, and stringified empty lists like '[]'
def no_ads(x):
    # None or NaN
    if pd.isna(x):
        return True
    
    # actual empty list/tuple/set
    if isinstance(x, (list, tuple, set)):
        return len(x) == 0
    
    # string forms: '', '[]', , 'None'
    s = str(x).strip()
    if s == '' or s == '[]' or s.lower() == 'none':
        return True
    
    return False

# creates a mask where False if ads is None
contains_no_ads = df['ads_symbols'].apply(no_ads)

df_only_h = df[contains_h_adsorbate]
df_only_h = df_only_h.reset_index(drop=True)

df_no_ads = df[contains_no_ads]
df_no_ads = df_no_ads.reset_index(drop=True)

df_only_h.to_csv("data/training_FULL_h.csv", index=False)
df_no_ads.to_csv("data/training_FULL_no_ads.csv", index=False)

# --------------------------------------------------------------
# randomly sample 100 data points from each dataset
# for the purpose of testing the featurizer. 
# remember to remove this section later

df_only_h_sample = df_only_h.sample(n=100)
df_no_ads_sample = df_no_ads.sample(n=100)
df_only_h_sample.to_csv("data/training_SAMPLE_h.csv", index=False)
df_no_ads_sample.to_csv("data/training_SAMPLE_no_ads.csv", index=False)

print(f"size of entire dataset: {df.shape}")
print(f"size of H-ads dataset: {df_only_h.shape}")
print(f"size of no-ads dataset: {df_no_ads.shape}")

size of entire dataset: (45890, 9)
size of H-ads dataset: (1605, 9)
size of no-ads dataset: (14646, 9)


In [44]:
# featurization
# use sample datasets to test the featurizers
h = df_only_h        # use df_only_h to process full dataset
no_ads = df_no_ads   # use df_no_ads to process full dataset

h_clean = h[['bulk_id', 'bulk_symbols', 'y_relaxed']]
no_ads_clean = no_ads[['bulk_id', 'bulk_symbols', 'y_relaxed']]

print(h_clean.head())
print(no_ads_clean.head())

         bulk_id bulk_symbols   y_relaxed
0  SbPdO4-rutile     Sb1Pd1O4 -531.043770
1        mp-8086     Na4Zn4O6 -135.378886
2     mp-1183298     Ba1Re1O3 -538.652121
3  FePdO4-rutile     Fe1Pd1O4 -387.021855
4        mp-2133        Zn2O2 -193.572049
      bulk_id bulk_symbols   y_relaxed
0    mp-11019     Ga2Cu2O4 -603.007638
1   mp-756297   Zn8In16O32 -576.660659
2     mp-2697        Sr2O4 -256.748952
3  mp-1183971     Cs1Ru1O3 -319.483107
4   mp-867628    Y6Cu11O24 -451.671846


In [5]:
# convert bulk symbols to Composition object
from pymatgen.core import Composition

pd.options.mode.copy_on_write = True
h_clean['bulk_symbols'] = h_clean['bulk_symbols'].apply(Composition)
no_ads_clean['bulk_symbols'] = no_ads_clean['bulk_symbols'].apply(Composition)

print("--- H-ads ---")
for c in h_clean['bulk_symbols'].head():
    print(f"formula: {c.formula}; num of atoms: {c.num_atoms}")

print("\n--- no-ads ---")
for c in no_ads_clean['bulk_symbols'].head():
    print(f"formula: {c.formula}; num of atoms: {c.num_atoms}")

--- H-ads ---
formula: Sb1 Pd1 O4; num of atoms: 6.0
formula: Na4 Zn4 O6; num of atoms: 14.0
formula: Ba1 Re1 O3; num of atoms: 5.0
formula: Fe1 Pd1 O4; num of atoms: 6.0
formula: Zn2 O2; num of atoms: 4.0

--- no-ads ---
formula: Ga2 Cu2 O4; num of atoms: 8.0
formula: Zn8 In16 O32; num of atoms: 56.0
formula: Sr2 O4; num of atoms: 6.0
formula: Cs1 Ru1 O3; num of atoms: 5.0
formula: Y6 Cu11 O24; num of atoms: 41.0


I think it is good to provide a good justification for which featurizers we use. 

I removed elemental fractions because the features are too sparse and creates high-dimensionality

In [6]:
from matminer.featurizers.composition import ElementProperty
from matminer.featurizers.composition import Stoichiometry
from matminer.featurizers.composition import ValenceOrbital
from matminer.featurizers.composition import TMetalFraction
from matminer.featurizers.composition import BandCenter
from matminer.featurizers.composition import CohesiveEnergy
from matminer.featurizers.composition import AtomicOrbitals

from dotenv import load_dotenv


# make sure to have your materials project api in the .env file
load_dotenv()
key = os.getenv('API_KEY')
print(f"API KEY: {key}")

def featurize_composition(df):
    featurized_df = df.copy()
    print("Initial df shape:", featurized_df.shape)
    
    featurizers = [
        ElementProperty.from_preset("magpie"),
        Stoichiometry(),
        ValenceOrbital(),
        TMetalFraction(),
        BandCenter(),
        # CohesiveEnergy(mapi_key=key),
        AtomicOrbitals(),
    ]

    for featurizer in featurizers:
        # featurizer.set_n_jobs(1)
        featurized_df = featurizer.featurize_dataframe(featurized_df, 'bulk_symbols')
    
    return featurized_df

API KEY: H1TcFfkjPB8IR4vjQB1vXdZ7CbceH5I4


In [7]:
import warnings


# suppress annoying warnings
warnings.filterwarnings('ignore', message='.*impute_nan.*')

# warning: this step can take a while!
h_comp_featurized = featurize_composition(h_clean)
no_ads_comp_featurized = featurize_composition(no_ads_clean)

Initial df shape: (1605, 3)


ElementProperty:   0%|          | 0/1605 [00:00<?, ?it/s]

Stoichiometry:   0%|          | 0/1605 [00:00<?, ?it/s]

ValenceOrbital:   0%|          | 0/1605 [00:00<?, ?it/s]

TMetalFraction:   0%|          | 0/1605 [00:00<?, ?it/s]

...

Stoichiometry:   0%|          | 0/14646 [00:00<?, ?it/s]

ValenceOrbital:   0%|          | 0/14646 [00:00<?, ?it/s]

TMetalFraction:   0%|          | 0/14646 [00:00<?, ?it/s]

BandCenter:   0%|          | 0/14646 [00:00<?, ?it/s]

AtomicOrbitals:   0%|          | 0/14646 [00:00<?, ?it/s]

In [8]:
h_comp_featurized.head()

bulk_id bulk_symbols   y_relaxed  MagpieData minimum Number  \
0  SbPdO4-rutile  (Sb, Pd, O) -531.043770                        8.0   
1        mp-8086  (Na, Zn, O) -135.378886                        8.0   
2     mp-1183298  (Ba, Re, O) -538.652121                        8.0   
3  FePdO4-rutile  (Fe, Pd, O) -387.021855                        8.0   
4        mp-2133      (Zn, O) -193.572049                        8.0   

   MagpieData maximum Number  MagpieData range Number  MagpieData mean Number  \
0                       51.0                     43.0               21.500000   
1                       30.0                     22.0               15.142857   
2                       75.0                     67.0               31.000000   
3                       46.0                     38.0               17.333333   
4                       30.0                     22.0               19.000000   

   MagpieData avg_dev Number  MagpieData mode Number  \
0                  18.000000                     8.0   
1                   8.489796                     8.0   
2                  27.600000                     8.0   
3                  12.444444                     8.0   
4                  11.000000                     8.0   

   MagpieData minimum MendeleevNumber  ...  frac f valence electrons  \
0                                62.0  ...                  0.000000   
1                                 2.0  ...                  0.000000   
2                                 9.0  ...                  0.341463   
3                                55.0  ...                  0.000000   
4                                69.0  ...                  0.000000   

   transition metal fraction  band center  HOMO_character  HOMO_element  \
0                   0.166667     6.416770               p            Sb   
1                   0.000000     4.984547               p             O   
2                   0.200000     5.403931               d            Re   
3                   0.333333     6.220992               d            Fe   
4                   0.000000     5.951264               p             O   

   HOMO_energy  LUMO_character  LUMO_element  LUMO_energy    gap_AO  
0    -0.185623               p            Sb    -0.185623  0.000000  
1    -0.338381               s            Zn    -0.222725  0.115656  
2    -0.258639               d            Re    -0.258639  0.000000  
3    -0.295049               s            Fe    -0.197978  0.097071  
4    -0.338381               s            Zn    -0.222725  0.115656  

[5 rows x 158 columns]

In [9]:
no_ads_comp_featurized.head()

bulk_id bulk_symbols   y_relaxed  MagpieData minimum Number  \
0    mp-11019  (Ga, Cu, O) -603.007638                        8.0   
1   mp-756297  (Zn, In, O) -576.660659                        8.0   
2     mp-2697      (Sr, O) -256.748952                        8.0   
3  mp-1183971  (Cs, Ru, O) -319.483107                        8.0   
4   mp-867628   (Y, Cu, O) -451.671846                        8.0   

   MagpieData maximum Number  MagpieData range Number  MagpieData mean Number  \
0                       31.0                     23.0               19.000000   
1                       49.0                     41.0               22.857143   
2                       38.0                     30.0               18.000000   
3                       55.0                     47.0               24.600000   
4                       39.0                     31.0               18.170732   

   MagpieData avg_dev Number  MagpieData mode Number  \
0                  11.000000                     8.0   
1                  16.979592                     8.0   
2                  13.333333                     8.0   
3                  19.920000                     8.0   
4                  11.907198                     8.0   

   MagpieData minimum MendeleevNumber  ...  frac f valence electrons  \
0                                64.0  ...                       0.0   
1                                69.0  ...                       0.0   
2                                 8.0  ...                       0.0   
3                                 5.0  ...                       0.0   
4                                12.0  ...                       0.0   

   transition metal fraction  band center  HOMO_character  HOMO_element  \
0                   0.250000     5.320929               d            Cu   
1                   0.000000     5.437784               p             O   
2                   0.000000     5.466758               p             O   
3                   0.200000     5.235859               d            Ru   
4                   0.268293     5.799601               d            Cu   

   HOMO_energy  LUMO_character  LUMO_element  LUMO_energy    gap_AO  
0    -0.202272               d            Cu    -0.202272  0.000000  
1    -0.338381               s            In    -0.290497  0.047884  
2    -0.338381               p             O    -0.338381  0.000000  
3    -0.210375               d            Ru    -0.210375  0.000000  
4    -0.202272               d            Cu    -0.202272  0.000000  

[5 rows x 158 columns]

In [45]:
h_comp_featurized.to_csv("data/training_FULL_h_comp_featurized.csv", index=False)
no_ads_comp_featurized.to_csv("data/training_FULL_no_ads_comp_featurized.csv", index=False)

possible MP fields that can be requested by API:

['builder_meta',
 'nsites',
 'elements',
 'nelements',
 'composition',
 'composition_reduced',
 'formula_pretty',
 'formula_anonymous',
 'chemsys',
 'volume',
 'density',
 'density_atomic',
 'symmetry',
 'deprecated',
 'deprecation_reasons',
 'last_updated',
 'origins',
 'warnings',
 'property_name',
 'task_ids',
 'uncorrected_energy_per_atom',
 'formation_energy_per_atom',
 'energy_above_hull',
 'is_stable',
 'equilibrium_reaction_energy_per_atom',
 'decomposes_to',
 'xas',
 'grain_boundaries',
 'band_gap',
 'cbm',
 'vbm',
 'efermi',
 'is_gap_direct',
 'is_metal',
 'es_source_calc_id',
 'bandstructure',
 'dos',
 'dos_energy_up',
 'dos_energy_down',
 'is_magnetic',
 'ordering',
 'total_magnetization',
 'total_magnetization_normalized_vol',
 'total_magnetization_normalized_formula_units',
 'num_magnetic_sites',
 'num_unique_magnetic_sites',
 'types_of_magnetic_species',
 'bulk_modulus',
 'shear_modulus',
 'universal_anisotropy',
 'homogeneous_poisson',
 'e_total',
 'e_ionic',
 'e_electronic',
 'n',
 'e_ij_max',
 'weighted_surface_energy_EV_PER_ANG2',
 'weighted_surface_energy',
 'weighted_work_function',
 'surface_anisotropy',
 'shape_factor',
 'has_reconstructed',
 'possible_species',
 'has_props',
 'theoretical',
 'database_IDs']

DensityFeatures:
- density
- vpa
- packing fraction

GlobalSymmetryFeatures:
- spacegroup_num
- crystal_system
- crystal_system_int
- is_centrosymmetric
- n_symmetry_ops

In [11]:
# get structure properties
from mp_api.client import MPRester


def fetch_structure(df):
    structures = []
    bulk_symbols_col = df['bulk_symbols']

    with MPRester(key) as mpr:
        for row in bulk_symbols_col:
            formula = row.reduced_formula

            try:
                # retrieve SummaryDoc
                docs = mpr.materials.summary.search(
                    formula=formula,
                    fields=['structure', 'energy_per_atom']
                )
                if docs:
                    best_doc = min(docs, key=lambda x: x.energy_per_atom)
                    best_structure = best_doc.structure
                    structures.append(best_structure)
                else:
                    structures.append(None)
                    print(f"unable to get structure for {formula}")
            except:
                structures.append(None)
                print(f"cannot unable to communicate with MP REST API: {formula}")
    
    result_df = df.copy().drop(columns=['bulk_id', 'y_relaxed'])
    result_df['structure'] = structures
    return result_df

In [12]:
h_structures = fetch_structure(h_clean)
no_ads_structures = fetch_structure(no_ads_clean)

Retrieving SummaryDoc documents: 0it [00:00, ?it/s]

unable to get structure for SbPdO4


Retrieving SummaryDoc documents:   0%|          | 0/2 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents: 0it [00:00, ?it/s]

...

Retrieving SummaryDoc documents:   0%|          | 0/6 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/3 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

In [46]:
# save structures to csv
h_structures.to_csv("data/FULL_h_structures.csv", index=False)
no_ads_structures.to_csv("data/FULL_no_ads_structures.csv", index=False)

In [14]:
from matminer.featurizers.structure import DensityFeatures 
from matminer.featurizers.structure import GlobalSymmetryFeatures
from matminer.featurizers.structure import SiteStatsFingerprint
from matminer.featurizers.structure import StructuralHeterogeneity
from matminer.featurizers.structure import MaximumPackingEfficiency
from matminer.featurizers.structure import ChemicalOrdering
from matminer.featurizers.structure import CoulombMatrix


def featurize_structure(df):
    featurized_df = df.copy()
    
    featurizers = [
        DensityFeatures(),
        GlobalSymmetryFeatures(),
        SiteStatsFingerprint.from_preset("LocalPropertyDifference_ward-prb-2017"),
        StructuralHeterogeneity(),
        MaximumPackingEfficiency(),
        ChemicalOrdering(),
    ]
    
    for featurizer in featurizers:
        # featurizer.set_n_jobs(1)
        featurized_df = featurizer.featurize_dataframe(
            featurized_df, 
            'structure', 
            ignore_errors=True
        )

    coulomb_matrix = CoulombMatrix(flatten=True)
    coulomb_matrix.fit(featurized_df['structure'].dropna().tolist())
    
    # coulomb_matrix.set_n_jobs(1)
    featurized_df = coulomb_matrix.featurize_dataframe(
        featurized_df,
        'structure',
        ignore_errors=True
    )
    
    return featurized_df

In [15]:
print("h-ads dataset: ")
h_structure_featurized = featurize_structure(h_structures)

print("no-ads dataset:")
no_ads_structure_featurized = featurize_structure(no_ads_structures)

h-ads dataset: 


DensityFeatures:   0%|          | 0/1605 [00:00<?, ?it/s]

GlobalSymmetryFeatures:   0%|          | 0/1605 [00:00<?, ?it/s]

SiteStatsFingerprint:   0%|          | 0/1605 [00:00<?, ?it/s]

StructuralHeterogeneity:   0%|          | 0/1605 [00:00<?, ?it/s]

...

StructuralHeterogeneity:   0%|          | 0/14646 [00:00<?, ?it/s]

MaximumPackingEfficiency:   0%|          | 0/14646 [00:00<?, ?it/s]

ChemicalOrdering:   0%|          | 0/14646 [00:00<?, ?it/s]

CoulombMatrix:   0%|          | 0/14646 [00:00<?, ?it/s]

/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discar

In [47]:
h_structure_featurized.to_csv("data/training_FULL_h_struct_featurized.csv", index=False)
no_ads_structure_featurized.to_csv("data/training_FULL_no_ads_struct_featurized.csv", index=False)

In [50]:
# combine composition and structure features
h_comp_merge = h_comp_featurized.set_index('bulk_symbols')
h_structure_merge = h_structure_featurized.set_index('bulk_symbols')
h_final = pd.concat([h_comp_merge, h_structure_merge], axis=1)

no_ads_comp_merge = no_ads_comp_featurized.set_index('bulk_symbols')
no_ads_structure_merge = no_ads_structure_featurized.set_index('bulk_symbols')
no_ads_final = pd.concat([no_ads_comp_merge, no_ads_structure_merge], axis=1)

print(h_final.shape)
print(no_ads_final.shape)

# here save the final fully featurized dataset.
h_final.to_csv("data/training_FULL_h_all_featurized.csv")
no_ads_final.to_csv("data/training_FULL_no_ads_all_featurized.csv")

(1605, 487)
(14646, 487)


In [51]:
h_final.head()

bulk_id   y_relaxed  MagpieData minimum Number  \
bulk_symbols                                                         
(Sb, Pd, O)   SbPdO4-rutile -531.043770                        8.0   
(Na, Zn, O)         mp-8086 -135.378886                        8.0   
(Ba, Re, O)      mp-1183298 -538.652121                        8.0   
(Fe, Pd, O)   FePdO4-rutile -387.021855                        8.0   
(Zn, O)             mp-2133 -193.572049                        8.0   

              MagpieData maximum Number  MagpieData range Number  \
bulk_symbols                                                       
(Sb, Pd, O)                        51.0                     43.0   
(Na, Zn, O)                        30.0                     22.0   
(Ba, Re, O)                        75.0                     67.0   
(Fe, Pd, O)                        46.0                     38.0   
(Zn, O)                            30.0                     22.0   

              MagpieData mean Number  MagpieData avg_dev Number  \
bulk_symbols                                                      
(Sb, Pd, O)                21.500000                  18.000000   
(Na, Zn, O)                15.142857                   8.489796   
(Ba, Re, O)                31.000000                  27.600000   
(Fe, Pd, O)                17.333333                  12.444444   
(Zn, O)                    19.000000                  11.000000   

              MagpieData mode Number  MagpieData minimum MendeleevNumber  \
bulk_symbols                                                               
(Sb, Pd, O)                      8.0                                62.0   
(Na, Zn, O)                      8.0                                 2.0   
(Ba, Re, O)                      8.0                                 9.0   
(Fe, Pd, O)                      8.0                                55.0   
(Zn, O)                          8.0                                69.0   

              MagpieData maximum MendeleevNumber  ...  coulomb matrix eig 188  \
bulk_symbols                                      ...                           
(Sb, Pd, O)                                 87.0  ...                     NaN   
(Na, Zn, O)                                 87.0  ...                     0.0   
(Ba, Re, O)                                 87.0  ...                     0.0   
(Fe, Pd, O)                                 87.0  ...                     NaN   
(Zn, O)                                     87.0  ...                     0.0   

              coulomb matrix eig 189  coulomb matrix eig 190  \
bulk_symbols                                                   
(Sb, Pd, O)                      NaN                     NaN   
(Na, Zn, O)                      0.0                     0.0   
(Ba, Re, O)                      0.0                     0.0   
(Fe, Pd, O)                      NaN                     NaN   
(Zn, O)                          0.0                     0.0   

              coulomb matrix eig 191  coulomb matrix eig 192  \
bulk_symbols                                                   
(Sb, Pd, O)                      NaN                     NaN   
(Na, Zn, O)                      0.0                     0.0   
(Ba, Re, O)                      0.0                     0.0   
(Fe, Pd, O)                      NaN                     NaN   
(Zn, O)                          0.0                     0.0   

              coulomb matrix eig 193  coulomb matrix eig 194  \
bulk_symbols                                                   
(Sb, Pd, O)                      NaN                     NaN   
(Na, Zn, O)                      0.0                     0.0   
(Ba, Re, O)                      0.0                     0.0   
(Fe, Pd, O)                      NaN                     NaN   
(Zn, O)                          0.0                     0.0   

              coulomb matrix eig 195  coulomb matrix eig 196  \
bulk_symbols                                                   
(Sb, P